In [1]:
import torch
torch.cuda.is_available()

True

In [2]:
import importlib
importlib.reload(torch)

<module 'torch' from '/home/raj/anaconda3/envs/test-cuda/lib/python3.7/site-packages/torch/__init__.py'>

In [3]:
from tqdm import tqdm

In [4]:
import logging
import math
import os
import random
import sys
import time
import pickle
import copy

import numpy as np
import torch

from fairseq import (
    checkpoint_utils,
    distributed_utils,
    options,
    quantization_utils,
    tasks,
    utils,
)
from fairseq.data import iterators
from fairseq.logging import meters, metrics, progress_bar
from fairseq.trainer import Trainer
from fairseq.model_parallel.megatron_trainer import MegatronTrainer
from fairseq.models.pruned_transformer import PrunedTransformerModel

In [5]:
args = pickle.load(open("argsfile.p", "rb"))

In [6]:
print(args)

Namespace(activation_dropout=0.0, activation_fn='relu', adam_betas='(0.9, 0.98)', adam_eps=1e-08, adaptive_input=False, adaptive_softmax_cutoff=None, adaptive_softmax_dropout=0, all_gather_list_size=16384, arch='pruned_transformer_vaswani_wmt_en_de_big', attention_dropout=0.0, best_checkpoint_metric='loss', bf16=False, bpe=None, broadcast_buffers=False, bucket_cap_mb=25, checkpoint_suffix='', clip_norm=0.0, cpu=False, criterion='label_smoothed_cross_entropy', cross_self_attention=False, curriculum=0, data='data-bin/wmt16_en_de_bpe32k', data_buffer_size=2, dataset_impl=None, ddp_backend='c10d', decoder_attention_heads=16, decoder_embed_dim=1024, decoder_embed_path=None, decoder_ffn_embed_dim=4096, decoder_input_dim=1024, decoder_layerdrop=0, decoder_layers=6, decoder_layers_to_keep=None, decoder_learned_pos=False, decoder_normalize_before=False, decoder_output_dim=1024, device_id=0, disable_validation=False, distributed_backend='nccl', distributed_init_method=None, distributed_no_spawn=

In [7]:
task = tasks.setup_task(args)

In [8]:
task.load_dataset(args.valid_subset, combine=False, epoch=1)
dataset = task.dataset(args.valid_subset)


In [9]:
checkpoint_dir = "/home/raj/data/raj-learn/checkpoints/lr-rewind_0.75sparsity_0.2frac_30epochs/"
model_paths = ["checkpoint_LTH0_epoch60.pt",
              "checkpoint_LTH1_epoch60_sparsity0.168.pt",
              "checkpoint_LTH2_epoch60_sparsity0.302.pt",
              "checkpoint_LTH3_epoch60_sparsity0.410.pt", 
              "checkpoint_LTH4_epoch60_sparsity0.496.pt", 
              "checkpoint_LTH5_epoch60_sparsity0.565.pt",
              "checkpoint_LTH6_epoch60_sparsity0.620.pt",
              "checkpoint_LTH7_epoch60_sparsity0.664.pt"]


In [10]:
args.path = checkpoint_dir + model_paths[0]

In [11]:
models, _model_args = checkpoint_utils.load_model_ensemble(
        args.path.split(os.pathsep),
        task=task,
    )
model = models[0]
model.cuda()
model.eval()

PrunedTransformerModel(
  (encoder): TransformerEncoder(
    (embed_tokens): Embedding(32768, 1024, padding_idx=1)
    (embed_positions): SinusoidalPositionalEmbedding()
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (k_proj): Linear(in_features=1024, out_features=1024, bias=True)
          (v_proj): Linear(in_features=1024, out_features=1024, bias=True)
          (q_proj): Linear(in_features=1024, out_features=1024, bias=True)
          (out_proj): Linear(in_features=1024, out_features=1024, bias=True)
        )
        (self_attn_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (fc1): Linear(in_features=1024, out_features=4096, bias=True)
        (fc2): Linear(in_features=4096, out_features=1024, bias=True)
        (final_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
      )
      (1): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (k_proj): 

In [12]:
print(model)

PrunedTransformerModel(
  (encoder): TransformerEncoder(
    (embed_tokens): Embedding(32768, 1024, padding_idx=1)
    (embed_positions): SinusoidalPositionalEmbedding()
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (k_proj): Linear(in_features=1024, out_features=1024, bias=True)
          (v_proj): Linear(in_features=1024, out_features=1024, bias=True)
          (q_proj): Linear(in_features=1024, out_features=1024, bias=True)
          (out_proj): Linear(in_features=1024, out_features=1024, bias=True)
        )
        (self_attn_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
        (fc1): Linear(in_features=1024, out_features=4096, bias=True)
        (fc2): Linear(in_features=4096, out_features=1024, bias=True)
        (final_layer_norm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
      )
      (1): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (k_proj): 

In [13]:
itr = task.get_batch_iterator(
            dataset=dataset,
            max_tokens=args.max_tokens,
            max_sentences=args.max_sentences,
            max_positions=utils.resolve_max_positions(
                task.max_positions(),
                *[m.max_positions() for m in models],
            ),
            ignore_invalid_inputs=args.skip_invalid_size_inputs_valid_test,
            required_batch_size_multiple=args.required_batch_size_multiple,
            seed=args.seed,
            num_shards=args.distributed_world_size,
            shard_id=args.distributed_rank,
            num_workers=args.num_workers,
        ).next_epoch_itr(shuffle=False)

In [20]:
all_masks = {}
for batch in tqdm(itr):
    ids = batch["id"].cpu().numpy().tolist()
    src_lens = batch["net_input"]["src_lengths"].cpu().numpy()
    enc_outputs = model.encoder(batch["net_input"]["src_tokens"].cuda(), batch["net_input"]["src_lengths"].cuda(), 
                                        return_all_hiddens=False, return_all_attns=True)
    #print(enc_outputs.encoder_self_attns[0].shape)
    encenc_attns = [x.detach().cpu().numpy() for x in enc_outputs.encoder_self_attns]
    del enc_outputs
    
    out, props = model(batch["net_input"]["src_tokens"].cuda(), batch["net_input"]["src_lengths"].cuda(), \
                        batch["net_input"]["prev_output_tokens"].cuda())
    encdec_attns = [x.detach().cpu().numpy() for x in props["encdec_attns"]]
    #print(encdec_attns[0].shape)
    decdec_attns = [x.detach().cpu().numpy() for x in props["decdec_attns"]]
    #print(decdec_attns[0].shape)

    print(batch["net_input"]["prev_output_tokens"].shape)
    print(batch["net_input"]["prev_output_tokens"][12,:])
    print(batch["target"][12,:])
    del out, props
    del batch

    for i, id_ in enumerate(ids):
        all_attns = {"encenc": [], "encdec": [], "decdec": []}
        for attn in encenc_attns:
            all_attns["encenc"].append(attn[i,:,:src_lens[i],:src_lens[i]])
        for attn in encdec_attns:
            all_attns["encdec"].append(attn[:,i,:src_lens[i],:])
            print(attn[3,i,:,:])
        for attn in decdec_attns:
            all_attns["decdec"].append(attn[i,:,:,:])
            #print(attn[i,3,:,:])
            break
        all_masks[id_] = all_attns
        
    break

  0%|          | 0/34 [00:00<?, ?it/s]

torch.Size([136, 26])
tensor([    2,    72,   111, 16622, 29731, 23264,    74,  2515,     4,   424,
           17,   156,   643,     5,     1,     1,     1,     1,     1,     1,
            1,     1,     1,     1,     1,     1])
tensor([   72,   111, 16622, 29731, 23264,    74,  2515,     4,   424,    17,
          156,   643,     5,     2,     1,     1,     1,     1,     1,     1,
            1,     1,     1,     1,     1,     1])
[[6.44680709e-02 1.30319642e-02 1.33994997e-01 1.64771825e-02
  3.13353240e-02 3.72480787e-02 6.63464330e-03 6.25620224e-03
  1.01139266e-02 4.62222891e-03 8.64710100e-03 2.27859430e-02
  1.01455815e-01 3.39323804e-02 7.54702836e-02 3.57667124e-03
  2.61400584e-02 4.03809100e-01]
 [3.54456641e-02 1.91950041e-03 1.63155109e-01 3.69472941e-03
  5.42121641e-02 3.29018086e-01 4.51200269e-02 5.59261302e-03
  1.99398212e-02 8.86640686e-04 2.14621914e-03 9.17469151e-03
  6.36401027e-02 3.65242288e-02 3.39171439e-02 8.08998290e-03
  8.93869088e-04 1.86629444e-01]
 [

[[2.95626726e-02 3.84699106e-02 3.39835882e-02 2.31781546e-02
  1.38113992e-02 8.73809680e-03 5.92476837e-02 1.38229150e-02
  5.21083921e-03 5.90737769e-03 2.34731454e-02 8.16957951e-02
  4.33978997e-02 1.00357775e-02 4.53032181e-03 3.29916552e-02
  2.85971254e-01 2.85971493e-01]
 [1.88370573e-03 1.32671441e-03 1.25826849e-03 9.12892574e-04
  6.75007002e-03 5.51937206e-04 7.35849328e-03 5.09666326e-03
  2.21117632e-03 2.00594030e-03 1.82644520e-02 9.36103519e-03
  1.43730855e-02 1.57603994e-03 3.14137829e-03 5.90639897e-02
  4.32431877e-01 4.32432353e-01]
 [1.57543942e-02 1.19615337e-02 6.49140403e-02 7.81167671e-02
  3.14155146e-02 5.32575604e-03 5.79586327e-02 2.30590310e-02
  2.00981298e-03 3.67851998e-03 2.48011667e-02 3.06150671e-02
  1.69480164e-02 1.60676904e-03 4.36629960e-03 3.34722064e-02
  2.96998262e-01 2.96998203e-01]
 [2.84360070e-03 4.08265041e-03 6.36863755e-03 1.81072280e-02
  2.17372105e-01 9.58252407e-04 4.26677242e-03 2.27792747e-02
  8.14423256e-04 4.22954239e-04 3

[[1.52546152e-01 4.16854210e-02 6.97175832e-03 3.61145325e-02
  2.99965069e-02 3.98129113e-02 1.22454735e-02 7.06700534e-02
  8.93906411e-03 4.78962017e-03 8.78470577e-03 3.80190127e-02
  6.69172928e-02 4.80874106e-02 1.16566513e-02 1.47501323e-02
  2.04006538e-01 2.04006732e-01]
 [1.11306250e-01 6.95597939e-03 1.57660376e-02 1.10953748e-02
  2.22952403e-02 2.87554353e-01 1.91219896e-02 4.59836513e-01
  3.00664548e-03 2.59539066e-03 6.43253606e-03 4.41928627e-04
  4.63464670e-02 1.18818274e-03 2.32329345e-04 1.20497670e-03
  2.30992842e-03 2.30992842e-03]
 [1.75926927e-02 3.74596263e-03 1.38833933e-03 7.75921810e-03
  9.05715569e-04 9.97387106e-04 1.42579037e-03 3.75320949e-03
  4.07026266e-04 1.31235411e-03 1.10131281e-03 2.15367624e-03
  1.76878017e-03 9.18686111e-03 8.91756208e-04 6.78447308e-04
  4.72465187e-01 4.72466201e-01]
 [1.65940449e-01 6.24532066e-03 1.23589970e-02 2.84729432e-02
  1.71654706e-03 3.22898664e-03 8.47914442e-03 7.68529065e-03
  1.00852584e-03 2.96957139e-03 2

[[7.46523514e-02 2.31290963e-02 2.56575420e-02 3.56624797e-02
  3.14016566e-02 5.55581823e-02 1.88412189e-01 3.80770825e-02
  4.90145665e-03 5.36496658e-03 1.06028281e-02 7.60625908e-03
  9.44404583e-03 4.13117278e-03 5.90997795e-03 2.31271833e-02
  2.28180736e-01 2.28180826e-01]
 [7.40740448e-02 6.62762951e-03 1.24198766e-02 1.44421193e-03
  2.76267016e-03 8.37432384e-01 1.10486313e-03 5.78780193e-03
  9.05234047e-05 4.21971636e-04 4.16734634e-04 2.73439160e-04
  1.06385560e-03 2.78615498e-05 4.37349314e-04 2.55734980e-04
  2.76795030e-02 2.76795626e-02]
 [3.74168530e-02 3.53681680e-04 8.00862617e-04 2.10316163e-02
  2.39462778e-02 8.12143147e-01 3.19208461e-03 5.66081470e-03
  1.90500228e-04 3.43897118e-04 4.45595477e-04 1.79517170e-04
  1.60807325e-03 1.14513059e-04 4.21872450e-04 4.47719544e-03
  4.38366607e-02 4.38367464e-02]
 [1.76113527e-02 1.70011492e-03 2.38437136e-03 1.31029207e-02
  4.14948352e-02 4.43477184e-01 6.19238522e-03 1.01114912e-02
  1.00961642e-03 5.69393567e-04 4

...

[[0.00000000e+00 2.71981508e-01 1.44409999e-01 1.11468822e-01
  4.48952205e-02 2.39498299e-02 4.13538627e-02 2.66055670e-02
  7.03037530e-03 4.05579479e-03 3.58454161e-03 1.14504609e-03
  5.25466986e-02 3.63930538e-02 1.80049539e-02 2.17514532e-03
  1.05199687e-01 1.05199941e-01]
 [0.00000000e+00 2.23684445e-01 1.99054517e-02 3.90916169e-02
  5.63621474e-03 4.39245906e-03 2.30657402e-02 1.87421252e-03
  2.70983092e-02 3.54167037e-02 7.79023161e-04 2.40928051e-03
  1.90285757e-01 3.08445722e-01 2.26114243e-02 9.99349728e-03
  4.26550284e-02 4.26551253e-02]
 [0.00000000e+00 2.37341467e-02 8.95457901e-03 6.64768647e-03
  2.89924964e-02 3.68933775e-03 3.16016153e-02 1.29879918e-04
  2.38724854e-02 3.42709683e-02 5.01227914e-04 2.65452126e-03
  4.03908594e-03 3.39393830e-03 4.94985618e-02 3.79597186e-03
  3.87111068e-01 3.87112319e-01]
 [0.00000000e+00 4.67113033e-02 1.01842470e-01 6.83388263e-02
  4.84288344e-03 1.30755035e-02 7.62699619e-02 1.41027421e-02
  6.76263794e-02 1.26106471e-01 1

[[0.00000000e+00 1.46455675e-01 1.45538583e-01 6.01757944e-01
  1.64520014e-02 3.30986571e-03 1.57597719e-03 2.03166506e-03
  2.54826341e-03 1.86776358e-03 1.22052887e-02 2.12479755e-03
  2.85460148e-04 1.10199885e-03 2.56921572e-04 4.22988599e-03
  2.91289147e-02 2.91289873e-02]
 [0.00000000e+00 5.84949739e-03 5.82590327e-03 2.72934977e-02
  6.83076726e-03 4.91831393e-04 3.74337629e-04 4.16144729e-04
  1.03885052e-03 1.10001711e-03 7.69157521e-03 1.62103039e-03
  3.16758960e-04 1.24285917e-03 3.52563988e-03 1.09622600e-02
  4.62708175e-01 4.62710857e-01]
 [0.00000000e+00 9.37077915e-04 6.82722079e-04 5.80111565e-03
  2.70593748e-03 1.28524587e-03 1.83093740e-04 3.18393228e-04
  3.79548455e-03 2.83933757e-03 7.13659683e-03 9.20155144e-04
  1.13797386e-03 2.89526815e-03 4.81823646e-03 6.12829626e-02
  4.51628834e-01 4.51631546e-01]
 [0.00000000e+00 9.15633235e-03 6.76476350e-03 1.68382712e-02
  9.34764668e-02 2.73308545e-01 2.28650987e-01 6.23833872e-02
  3.34902760e-03 1.26585141e-02 4

[[0.00000000e+00 0.00000000e+00 1.36200143e-02 1.18703200e-02
  8.61884747e-03 1.17277587e-02 7.69982301e-03 1.76572502e-02
  1.88336652e-02 2.53025163e-02 2.88736075e-02 5.74341826e-02
  1.28066137e-01 1.39172468e-02 6.15634443e-03 1.43539906e-02
  3.17933798e-01 3.17934483e-01]
 [0.00000000e+00 0.00000000e+00 3.56087163e-02 2.19082385e-01
  1.49142578e-01 4.52612117e-02 2.88392663e-01 1.41814211e-02
  3.72573026e-02 5.27329743e-03 2.27315119e-03 8.45222920e-03
  7.12882206e-02 9.41932388e-03 6.76223636e-03 9.13507584e-03
  4.92350161e-02 4.92351502e-02]
 [0.00000000e+00 0.00000000e+00 3.74360122e-02 4.57544833e-01
  3.47922534e-01 2.79380307e-02 1.46134263e-02 2.27800012e-03
  1.20796440e-02 2.28952593e-03 6.34158205e-04 9.67229903e-03
  1.83667394e-03 5.67873288e-03 3.70097405e-04 1.74764288e-03
  3.89791168e-02 3.89792174e-02]
 [0.00000000e+00 0.00000000e+00 2.73937751e-02 1.78386331e-01
  1.81384996e-01 1.33801550e-01 2.13156510e-02 1.64123476e-02
  7.16837719e-02 1.58671569e-02 4

  0%|          | 0/34 [00:06<?, ?it/s]

[[0.00000000e+00 0.00000000e+00 2.84310520e-01 8.53676721e-02
  1.28379874e-02 3.77498902e-02 1.49827991e-02 4.59151044e-02
  3.54608265e-03 2.86389291e-02 2.64358446e-02 5.13325259e-02
  7.23389117e-03 2.18364689e-02 9.72522888e-03 3.02762701e-03
  1.83529437e-01 1.83530003e-01]
 [0.00000000e+00 0.00000000e+00 1.51185542e-01 1.89477161e-01
  2.35450640e-01 1.30833462e-01 1.21420555e-01 3.31639014e-02
  4.17530304e-03 2.48194132e-02 4.03000042e-03 1.11709151e-03
  6.06785621e-03 1.92388333e-03 1.79493485e-03 1.88814080e-03
  4.63260375e-02 4.63261381e-02]
 [0.00000000e+00 0.00000000e+00 1.47792390e-02 5.18879555e-02
  1.37596885e-02 8.92340839e-02 1.42797856e-02 3.53979953e-02
  2.91535910e-03 1.65682808e-02 1.16935680e-02 3.30615379e-02
  1.59805198e-03 3.87833752e-02 5.13054756e-03 7.76530243e-04
  3.35066080e-01 3.35067838e-01]
 [0.00000000e+00 0.00000000e+00 3.61702703e-02 2.62467302e-02
  1.09760329e-01 3.78172658e-02 4.89097871e-02 3.56342018e-01
  1.78399589e-02 1.25315085e-01 1

In [15]:
for id_, mask in all_masks.items():
    print(len(mask["encdec"]))
    print(mask["encdec"][0].shape)
    print(np.sum(mask["encdec"][0][0,0,:]))
    break

6
(16, 9, 9)
0.9999999
